In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_operating_profit_sii = generate_df_for_stocktype(107, 2, 3, 'sii', 'OperationProfit', '營業利益率(%)(營業利益)/(營業收入)', '營益分析彙總表')

df_operating_profit_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業利益率(%)(營業利益)/(營業收入)
year: 107
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 2
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 2
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 2


公司代號     公司名稱 OperationProfit(%)_107Q2 OperationProfit(%)_107Q1  \
0    1101       台泥                    23.70                    19.23   
1    1102       亞泥                    19.80                    16.13   
2    1103       嘉泥                    -2.18                   -10.75   
3    1104     環球水泥                     3.09                     4.24   
4    1108     幸福水泥                    -1.94                    -4.15   
5    1109     信大水泥                    22.50                    13.71   
6    1110       東泥                     2.08                     1.83   
7    1201     味全公司                     1.42                    -0.59   
8    1203     味王公司                    15.01                    18.05   
9    1210     大成長城                     3.19                     3.42   
10   1213       大飲                     0.39                     0.77   
11   1215     卜蜂企業                     5.62                     6.68   
12   1216       統一                     6.92                     6.72   
13   1217      愛之味                     2.23                     3.33   
14   1218     泰山企業                     1.19                     0.98   
15   1219     福壽實業                     1.32                     2.01   
16   1220       台榮                     5.10                     3.01   
17   1225      福懋油                     3.65                     3.81   
18   1227       佳格                    10.09                    13.09   
19   1229     聯華實業                     5.70                     5.87   
20   1231     聯華食品                     5.81                     7.47   
21   1232      大統益                     6.28                     6.20   
22   1233       天仁                     8.67                     9.15   
23   1234       黑松                     0.66                    -1.31   
24   1235       興泰                   -60.86                   -74.18   
25   1236     宏亞食品                    -2.51                     5.90   
26   1256  鮮活果汁-KY                    17.31                    14.08   
27   1262    綠悅-KY                    -7.29                    -0.38   
28   1301       台塑                    13.07                    12.32   
29   1303     南亞塑膠                    10.60                    11.03   
30   1304       台聚                     5.98                     6.22   
31   1305       華夏                    15.08                    15.84   
32   1307     三芳化工                     3.85                     6.57   
33   1308       亞聚                     1.22                     2.04   
34   1309     台達化工                     4.12                     4.00   
35   1310       台苯                    11.39                    10.62   
36   1312     國喬石化                    12.18                    12.19   
37   1313       聯成                     3.04                     3.57   
38   1314      中石化                     9.06                     8.47   
39   1315     達新工業                    -2.65                    -1.94   
40   1316       上曜                    17.42                    17.82   
41   1319       東陽                     8.24                     9.49   
42   1321       大洋                    -3.68                    -1.05   
43   1323       永裕                    12.66                    11.60   
44   1324     地球工業                     0.12                    -2.64   
45   1325       恒大                     5.32                     6.02   
46   1326       台化                    11.39                    12.21   
47   1337    再生-KY                   -40.17                   -41.31   
48   1338    廣華-KY                     9.60                    10.27   
49   1339       昭輝                    13.67                    15.97   
50   1340    勝悅-KY                    14.57                    16.15   
51   1402      遠東新                     8.06                     6.79   
52   1410       南染                    22.39                    22.60   
53   1413     宏洲纖維                     6.30                     5.93   
54   1414       東和                     1.34  

In [5]:
df_operating_profit_otc = generate_df_for_stocktype(107, 2, 3, 'otc', 'OperationProfit', '營業利益率(%)(營業利益)/(營業收入)', '營益分析彙總表')

df_operating_profit_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業利益率(%)(營業利益)/(營業收入)
year: 107
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 2
營業利益率(%)(營業利益)/(營業收入)
year: 106
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 2
營業利益率(%)(營業利益)/(營業收入)
year: 105
season: 1
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 4
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 3
營業利益率(%)(營業利益)/(營業收入)
year: 104
season: 2


公司代號    公司名稱 OperationProfit(%)_107Q2 OperationProfit(%)_107Q1  \
0    1258   其祥-KY                     1.76                     2.70   
1    1259      安心                     3.21                     2.33   
2    1264      德麥                    16.98                    16.84   
3    1333     恩得利                   -55.05                   -58.94   
4    1336      台翰                     5.89                     6.34   
5    1565    精華光學                    29.63                    29.62   
6    1566      捷邦                     2.01                     2.34   
7    1569      濱川                     4.60                     4.89   
8    1570    力肯實業                    11.86                     9.48   
9    1580    新麥企業                    13.80                    12.52   
10   1584    精剛精密                   -12.20                    -8.95   
11   1586    和勤精機                     6.80                     4.70   
12   1591   駿吉-KY                     4.47                    -0.52   
13   1593      祺驊                     9.03                     6.58   
14   1595    川寶科技                    10.55                    10.32   
15   1597      直得                    28.36                    27.20   
16   1599     宏佳騰                     0.50                    -5.44   
17   1742      台蠟                   -28.30                    -7.88   
18   1752      南光                     9.79                    11.16   
19   1777      生泰                    20.05                    20.83   
20   1781    合世生醫                   -12.43                   -26.11   
21   1784    訊聯生技                     6.10                    11.66   
22   1785     光洋科                     2.73                     1.82   
23   1787     福盈科                     8.79                     8.63   
24   1788    杏昌生技                    10.03                     9.42   
25   1795    美時製藥                     5.41                     4.63   
26   1799      易威                   -75.97                   -67.91   
27   1813     寶利徠                    -5.35                    -5.81   
28   1815    富喬工業                    14.47                    14.86   
29   2035    唐榮公司                    -2.81                    -3.80   
30   2061      風青                     1.50                     1.57   
31   2063      世鎧                    19.25                    20.54   
32   2064      晉椿                     3.04                     4.28   
33   2066      世德                    12.33                    11.18   
34   2067      嘉鋼                     3.40                     1.77   
35   2221    大甲永和                    15.39                    14.01   
36   2230      泰茂                     1.21                    -4.62   
37   2233      宇隆                    23.02                    24.87   
38   2235      謚源                    11.18                    12.79   
39   2596    綠意開發                    35.62                    39.35   
40   2640     大車隊                    16.09                    17.77   
41   2641    正德海運                    15.85                    15.97   
42   2643      捷迅                     2.60                     2.35   
43   2718      晶悅                   -11.67                    -3.39   
44   2719     燦星旅                    -4.09                    -8.36   
45   2724   富驛-KY                   -19.51                   -34.04   
46   2726   雅茗-KY                     6.52                     6.94   
47   2729    瓦城泰統                    10.95                    10.62   
48   2732    六角國際                     5.85                     4.16   
49   2734     易飛網                    -6.00                    -4.65   
50   2736      高野                    -6.40                    -1.51   
51   2740      天蔥                   -10.95                   -12.01   
52   2916    滿心企業                     6.63                     7.23   
53   2924   東凌-KY                   -16.45                   -16.81   
54   2926    誠品生活                     8.90                    12.37   
55   3064    泰偉電子            

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_operating_profit = pd.concat([df_operating_profit_sii,df_operating_profit_otc],axis=0, ignore_index=True)

df_operating_profit

公司代號     公司名稱 OperationProfit(%)_107Q2 OperationProfit(%)_107Q1  \
0     1101       台泥                    23.70                    19.23   
1     1102       亞泥                    19.80                    16.13   
2     1103       嘉泥                    -2.18                   -10.75   
3     1104     環球水泥                     3.09                     4.24   
4     1108     幸福水泥                    -1.94                    -4.15   
5     1109     信大水泥                    22.50                    13.71   
6     1110       東泥                     2.08                     1.83   
7     1201     味全公司                     1.42                    -0.59   
8     1203     味王公司                    15.01                    18.05   
9     1210     大成長城                     3.19                     3.42   
10    1213       大飲                     0.39                     0.77   
11    1215     卜蜂企業                     5.62                     6.68   
12    1216       統一                     6.92                     6.72   
13    1217      愛之味                     2.23                     3.33   
14    1218     泰山企業                     1.19                     0.98   
15    1219     福壽實業                     1.32                     2.01   
16    1220       台榮                     5.10                     3.01   
17    1225      福懋油                     3.65                     3.81   
18    1227       佳格                    10.09                    13.09   
19    1229     聯華實業                     5.70                     5.87   
20    1231     聯華食品                     5.81                     7.47   
21    1232      大統益                     6.28                     6.20   
22    1233       天仁                     8.67                     9.15   
23    1234       黑松                     0.66                    -1.31   
24    1235       興泰                   -60.86                   -74.18   
25    1236     宏亞食品                    -2.51                     5.90   
26    1256  鮮活果汁-KY                    17.31                    14.08   
27    1262    綠悅-KY                    -7.29                    -0.38   
28    1301       台塑                    13.07                    12.32   
29    1303     南亞塑膠                    10.60                    11.03   
30    1304       台聚                     5.98                     6.22   
31    1305       華夏                    15.08                    15.84   
32    1307     三芳化工                     3.85                     6.57   
33    1308       亞聚                     1.22                     2.04   
34    1309     台達化工                     4.12                     4.00   
35    1310       台苯                    11.39                    10.62   
36    1312     國喬石化                    12.18                    12.19   
37    1313       聯成                     3.04                     3.57   
38    1314      中石化                     9.06                     8.47   
39    1315     達新工業                    -2.65                    -1.94   
40    1316       上曜                    17.42                    17.82   
41    1319       東陽                     8.24                     9.49   
42    1321       大洋                    -3.68                    -1.05   
43    1323       永裕                    12.66                    11.60   
44    1324     地球工業                     0.12                    -2.64   
45    1325       恒大                     5.32                     6.02   
46    1326       台化                    11.39                    12.21   
47    1337    再生-KY                   -40.17                   -41.31   
48    1338    廣華-KY                     9.60                    10.27   
49    1339       昭輝                    13.67                    15.97   
50    1340    勝悅-KY                    14.57                    16.15   
51    1402      遠東新                     8.06                     6.79   
52    1410       南染                    22.39                    22.60   
53    1413     宏洲纖維                     6.30                    

In [7]:
#檢查column資料型態

#df_operating_profit.info() #non-null object
#df_operating_profit.dtypes #object
#df_operating_profit.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
OperationProfit(%)_107Q1    float64
OperationProfit(%)_106Q4    float64
OperationProfit(%)_106Q3    float64
OperationProfit(%)_106Q2    float64
OperationProfit(%)_106Q1    float64
OperationProfit(%)_105Q4    float64
OperationProfit(%)_105Q3    float64
OperationProfit(%)_105Q2    float64
OperationProfit(%)_105Q1    float64
OperationProfit(%)_104Q4    float64
OperationProfit(%)_104Q3    float64
OperationProfit(%)_104Q2    float64
OperationProfit(%)_104Q1    float64
dtype: object
'''

df_operating_profit = df_operating_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_operating_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                          int64
公司名稱                         object
OperationProfit(%)_107Q2    float64
OperationProfit(%)_107Q1    float64
OperationProfit(%)_106Q4    float64
OperationProfit(%)_106Q3    float64
OperationProfit(%)_106Q2    float64
OperationProfit(%)_106Q1    float64
OperationProfit(%)_105Q4    float64
OperationProfit(%)_105Q3    float64
OperationProfit(%)_105Q2    float64
OperationProfit(%)_105Q1    float64
OperationProfit(%)_104Q4    float64
OperationProfit(%)_104Q3    float64
OperationProfit(%)_104Q2    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['OperationProfit(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['OperationProfit(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['OperationProfit(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['OperationProfit(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_operating_profit['Growth_{0}Q{1}'.format(year, season)] = df_operating_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_operating_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_operating_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_operating_profit = df_operating_profit.merge(df_basicinfo, on='公司代號', how='inner')

df_operating_profit

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  OperationProfit(%)_107Q2  OperationProfit(%)_107Q1  \
0     1101       台泥                     23.70                     19.23   
1     1102       亞泥                     19.80                     16.13   
2     1103       嘉泥                     -2.18                    -10.75   
3     1104     環球水泥                      3.09                      4.24   
4     1108     幸福水泥                     -1.94                     -4.15   
5     1109     信大水泥                     22.50                     13.71   
6     1110       東泥                      2.08                      1.83   
7     1201     味全公司                      1.42                     -0.59   
8     1203     味王公司                     15.01                     18.05   
9     1210     大成長城                      3.19                      3.42   
10    1213       大飲                      0.39                      0.77   
11    1215     卜蜂企業                      5.62                      6.68   
12    1216       統一                      6.92                      6.72   
13    1217      愛之味                      2.23                      3.33   
14    1218     泰山企業                      1.19                      0.98   
15    1219     福壽實業                      1.32                      2.01   
16    1220       台榮                      5.10                      3.01   
17    1225      福懋油                      3.65                      3.81   
18    1227       佳格                     10.09                     13.09   
19    1229     聯華實業                      5.70                      5.87   
20    1231     聯華食品                      5.81                      7.47   
21    1232      大統益                      6.28                      6.20   
22    1233       天仁                      8.67                      9.15   
23    1234       黑松                      0.66                     -1.31   
24    1235       興泰                    -60.86                    -74.18   
25    1236     宏亞食品                     -2.51                      5.90   
26    1256  鮮活果汁-KY                     17.31                     14.08   
27    1262    綠悅-KY                     -7.29                     -0.38   
28    1301       台塑                     13.07                     12.32   
29    1303     南亞塑膠                     10.60                     11.03   
30    1304       台聚                      5.98                      6.22   
31    1305       華夏                     15.08                     15.84   
32    1307     三芳化工                      3.85                      6.57   
33    1308       亞聚                      1.22                      2.04   
34    1309     台達化工                      4.12                      4.00   
35    1310       台苯                     11.39                     10.62   
36    1312     國喬石化                     12.18                     12.19   
37    1313       聯成                      3.04                      3.57   
38    1314      中石化                      9.06                      8.47   
39    1315     達新工業                     -2.65                     -1.94   
40    1316       上曜                     17.42                     17.82   
41    1319       東陽                      8.24                      9.49   
42    1321       大洋                     -3.68                     -1.05   
43    1323       永裕                     12.66                     11.60   
44    1324     地球工業                      0.12                     -2.64   
45    1325       恒大                      5.32                      6.02   
46    1326       台化                     11.39                     12.21   
47    1337    再生-KY                    -40.17                    -41.31   
48    1338    廣華-KY                      9.60                     10.27   
49    1339       昭輝                     13.67                     15.97   
50    1340    勝悅-KY                     14.57                     16.15   
51    1402      遠東新                      8.06                      6.79   
52    1410       南染            

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_operating_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_OperationProfit.xlsx', 'OperationProfit_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
